In [1]:
import pandas as pd
import glob
import cv2
import numpy as np
import matplotlib.pyplot as plt


In [4]:

class Image:

    def __init__(self) -> None:
        pass

    def get_block_mst(self,image,row,column):
        ht, wd = image.shape
        ch = 0 
        cw = 0
        nh = ht//row
        nw = wd//column
        ls = []
        m = nh

        if cw == 0:
            cri = image[ch:nh,cw:nw]
            # print(type(cri))
            ls.append(cri)
            # print(ls)
        n = nw
        for j in range(2,column+1):
            cw = nw
            nw = n*j
            cri = image[ch:nh,cw:nw]
            ls.append(cri) 
        for i in range(0,row):
            if i > 0:
                rc = i+1
                #print(i)
                ch = nh
                nh = m * rc
                cw = 0
                nw = nw//column
                if cw == 0:
                    cri = image[ch:nh,cw:nw]
                    ls.append(cri)
                n = nw
                for j in range(2,column+1):
                    cw = nw
                    nw = n*j
                    cri = image[ch:nh,cw:nw]
                    ls.append(cri)
        return ls     
            
    def get_block(self,image,row,column):
        img = cv2.imread(image,0)
        ht, wd = img.shape
        ch = 0 
        cw = 0
        nh = ht//row
        nw = wd//column
        ls = []
        m = nh

        if cw == 0:
            cri = img[ch:nh,cw:nw]
            # print(type(cri))
            ls.append(cri)
        n = nw
        for j in range(2,column+1):
            cw = nw
            nw = n*j
            cri = img[ch:nh,cw:nw]
            ls.append(cri) 
        for i in range(0,row):
            if i > 0:
                rc = i+1
                #print(i)
                ch = nh
                nh = m * rc
                cw = 0
                nw = nw//column
                if cw == 0:
                    cri = img[ch:nh,cw:nw]
                    ls.append(cri)
                n = nw
                for j in range(2,column+1):
                    cw = nw
                    nw = n*j
                    cri = img[ch:nh,cw:nw]
                    ls.append(cri)
            #i = i+1
        return ls 

    def avg_block_diff(self,block1,block2):
        ht1 , wd1 = block1.shape
        ht2 , wd2 = block2.shape

        a = np.mean(block1)
        b = np.mean(block2)
        avg = a - b
        return avg


    def align(self,refx,refy,x1,y1,image):
        img = cv2.imread(image,0)
        rows, cols = img.shape
        if (refx==x1) and (refy==y1):
            #print('Same')
            return img
            #plt.imshow(img)
        else:
            difx= refx - x1
            dify = refy - y1
            if (dify>0):
                crop_img = img[0:rows,(cols-dify):cols]
                img = img[0:rows,0:(cols-dify)]
                im_h = cv2.hconcat([crop_img, img])
                #plt.imshow(im_h)
                img = im_h
                #return im_h
            elif (dify<0):
                dify = abs(dify)
                crop_img = img[0:rows,0:dify]
                img = img[0:rows,dify:cols]
                im_h = cv2.hconcat([img,crop_img])
                img = im_h
                #plt.imshow(im_h)
                #return im_h
            if (difx>0):
                crop_img = img[0:difx,0:cols]
                img = img[difx:rows,0:cols]
                im_v = cv2.vconcat([img,crop_img])
                img = im_v
                #plt.imshow(im_v)
                #return im_v
            elif (difx<0):
                difx = abs(difx)
                crop_img = img[(rows-difx):rows,0:cols]
                img = img[0:(rows-difx),0:cols]
                im_v = cv2.vconcat([crop_img, img])
                img = im_v
                #plt.imshow(im_v)
            return img

def main():

    obj = Image()

    excel_path = '/home/office5/Desktop/TESTING/points.csv'
    df = pd.read_csv(excel_path)

    # Aligninig image
    crped_img = []
    path = '/home/office5/Desktop/TESTING/'
    refx, refy = df['midx'].iloc[0], df['midy'].iloc[0]
    for i in range(len(df.index)):
        img = df['File name'].iloc[i]
        img = f'{path}/{img}'
        x1, y1 = df['midx'].iloc[i], df['midy'].iloc[i]
        crped_img.append(obj.align(refx,refy,x1,y1,img))

    # print(crped_img[0][1][1])
        
    hei,wid = crped_img[0].shape
    master_img = np.zeros([hei, wid])
    for i in range(hei):
        for j in range(wid):
            master_img[i,j] = 0
            for k in range(len(df.index)):
                master_img[i,j] += (int(crped_img[k][i,j]))
            master_img[i,j] = master_img[i,j] / len(crped_img)

    height,width = 4,3 
    
    ac = []
    ac.append(obj.get_block_mst(master_img,height,width))

    lst = []
    for i in range(len(df.index)):
        img1 = df['File name'].iloc[i]
        img1 = f'{path}/{img1}'   
        each_blk = obj.get_block(img1,height,width)
        lst.append(each_blk)


    import time
    for i in range(len(lst)):
        start = time.time()
        lst1 = []
        for j in range(len(lst[1])):
            lst1.append(obj.avg_block_diff(ac[0][j],lst[i][j]))
        print(f"Difference between master_img and {df['File name'].iloc[i]}")
        end = time.time()
        print("time difference is ",end - start)
        print(lst1)
        print('\n')

main()

(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
(784, 2432)
Difference between master_img and Anna2.bmp
time difference is  0.04288768768310547
[0.026805662217810777, 0.12491650081365435, 0.0697438844668028, -0.004326675727597262, -0.0013130549974107453, -0.04611746687957918, -0.0164256481432119, 0.04730354596458142, -0.026024455622291498, 0.09873597025578817, 0.021520201703125963, 0.037675766058455906]


Difference between master_img and Anna3.bmp
time difference is  0.04274439811706543
[-0.015994733022509422, 0.06148399376478153, 0.018020162494465808, 0.03924993460402959, 0.17332065539463315, 0.07098034880918647, -0.021944117866624424, 0.15287981224412306, 0.11498130934816686, 0.05613959371174815, 0.1

Difference between master_img and Anna26.bmp
time difference is  0.04541325569152832
[0.052043142078176174, 0.18802278773631542, 0.06277945190100809, 0.009629461826108354, -0.07918106486583554, -0.012470640550361622, 0.180900290867271, 0.15839198833165824, -0.07891984280676922, -0.09529157908632158, -0.13394728956970425, -0.12438116197591853]


Difference between master_img and Anna27.bmp
time difference is  0.05121588706970215
[-0.07920119364952427, -0.20164767748924817, -0.11471733834468978, -0.10990189306782838, -0.2846425771845702, -0.1663631494453739, -0.009839882669254507, -0.0967829537668905, -0.04530448465692416, -0.11708696459248813, -0.19956263932802187, -0.1653973114455738]


Difference between master_img and Anna28.bmp
time difference is  0.0410764217376709
[-0.08431424832863854, -0.09975528607543538, -0.08280598210811263, -0.07996936084440165, -0.28488383322647337, -0.15725835621229578, -0.057264526869033716, -0.2797982137360009, -0.23558102701728956, -0.09541168263760369,

In [48]:
print(ac[0][1],lst[0][1])

NameError: name 'ac' is not defined

In [49]:
def align(refx,refy,x1,y1,image):
    img = cv2.imread(image,0)
    rows, cols = img.shape
    if (refx==x1) and (refy==y1):
        #print('Same')
        return img
        #plt.imshow(img)
    else:
        difx= refx - x1
        dify = refy - y1
        if (dify>0):
            crop_img = img[0:rows,(cols-dify):cols]
            img = img[0:rows,0:(cols-dify)]
            im_h = cv2.hconcat([crop_img, img])
            #plt.imshow(im_h)
            img = im_h
            #return im_h
        elif (dify<0):
            dify = abs(dify)
            crop_img = img[0:rows,0:dify]
            img = img[0:rows,dify:cols]
            im_h = cv2.hconcat([img,crop_img])
            img = im_h
            #plt.imshow(im_h)
            #return im_h
        if (difx>0):
            crop_img = img[0:difx,0:cols]
            img = img[difx:rows,0:cols]
            im_v = cv2.vconcat([img,crop_img])
            img = im_v
            #plt.imshow(im_v)
            #return im_v
        elif (difx<0):
            difx = abs(difx)
            crop_img = img[(rows-difx):rows,0:cols]
            img = img[0:(rows-difx),0:cols]
            im_v = cv2.vconcat([crop_img, img])
            img = im_v
            #plt.imshow(im_v)
        return img

In [51]:
excel_path = '/home/office5/Desktop/TESTING/test.csv'
df = pd.read_csv(excel_path)

img_giv_pth = "/home/office5/Desktop/TESTING/*.bmp"
img_pth = glob.glob(img_giv_pth)


# Aligninig image
avg_all = []

crped_img = []
path = '/home/office5/Desktop/TESTING/'
refx, refy = df['midx'].iloc[0], df['midy'].iloc[0]
for i in range(len(df.index)):
    img = df['File name'].iloc[i]
    img = f'{path}/{img}'
    x1, y1 = df['midx'].iloc[i], df['midy'].iloc[i]
    crped_img.append(align(refx,refy,x1,y1,img))

# print(crped_img[0][1][1])


In [54]:
    
hei,wid = 3136 ,7296
master_img = np.zeros([hei, wid])
for i in range(hei):
    for j in range(wid):
        master_img[i,j] = 0
        # master_img[i,j]  = (int(img_name[0][i,j]) + int(img_name[1][i,j]) + int(img_name[2][i,j]) + int(img_name[3][i,j])) 
        for k in range(len(df.index)):
            master_img[i,j] += (int(crped_img[k][i,j]))
            print(crped_img[k][i,j],i,j,k,master_img[i,j])
        master_img[i,j] = master_img[i,j] / len(crped_img)
        

    # if(i==10):
    #     break

86 0 0 0 86.0
84 0 0 1 170.0
97 0 0 2 267.0
95 0 0 3 362.0
82 0 1 0 82.0
82 0 1 1 164.0
85 0 1 2 249.0
85 0 1 3 334.0
85 0 2 0 85.0
85 0 2 1 170.0
84 0 2 2 254.0
84 0 2 3 338.0
85 0 3 0 85.0
82 0 3 1 167.0
84 0 3 2 251.0
85 0 3 3 336.0
86 0 4 0 86.0
85 0 4 1 171.0
80 0 4 2 251.0
85 0 4 3 336.0
84 0 5 0 84.0
82 0 5 1 166.0
84 0 5 2 250.0
85 0 5 3 335.0
82 0 6 0 82.0
84 0 6 1 166.0
84 0 6 2 250.0
82 0 6 3 332.0
83 0 7 0 83.0
84 0 7 1 167.0
85 0 7 2 252.0
84 0 7 3 336.0
84 0 8 0 84.0
82 0 8 1 166.0
86 0 8 2 252.0
82 0 8 3 334.0
82 0 9 0 82.0
84 0 9 1 166.0
85 0 9 2 251.0
84 0 9 3 335.0
82 0 10 0 82.0
85 0 10 1 167.0
86 0 10 2 253.0
82 0 10 3 335.0
84 0 11 0 84.0
82 0 11 1 166.0
81 0 11 2 247.0
84 0 11 3 331.0
85 0 12 0 85.0
84 0 12 1 169.0
84 0 12 2 253.0
84 0 12 3 337.0
83 0 13 0 83.0
80 0 13 1 163.0
84 0 13 2 247.0
82 0 13 3 329.0
86 0 14 0 86.0
82 0 14 1 168.0
84 0 14 2 252.0
82 0 14 3 334.0
82 0 15 0 82.0
84 0 15 1 166.0
81 0 15 2 247.0
80 0 15 3 327.0
85 0 16 0 85.0
82 0 16 1 167.0
8

KeyboardInterrupt: 

In [53]:
print(master_img[3135][7295])

0.0


In [21]:
print(len(crped_img))

4


In [27]:
hei,wid = 3136 ,7296
master_img = np.zeros([hei, wid])

In [29]:
print(len(df.index))

4


In [28]:
master_img.shape

(3136, 7296)

In [30]:
print(crped_img[0][0][0])
print(master_img[3131][3131])

86
0.0
